In [1]:
import plotly
import cufflinks
import plotly.offline as py
import plotly.graph_objs as go
import plotly.express as px
import pandas as pd
import numpy as np
import cvxopt as opt
from cvxopt import blas, solvers
pd.set_option('display.max_columns', None) # coluna
pd.set_option('display.max_rows', None) # linha
py.init_notebook_mode(connected=True)

plotly.__version__

'5.15.0'

Esse notebook tem a intenção de processar as rotinas 01.05.07.04.02 e 12.06.59, de forma a processar cada PDV com Prazo como um ativo de investimento, calcular seus retornos e modelar a carteira de crédito da Ambev-GEO CO como uma carteira de investimentos

In [2]:
df = pd.read_excel(r"C:/Users/99829465/Documents/0105070402 - full.xlsx")
df.head(10)

Empresa  Filial  Cód PDV           Documento  \
0        3      77        1  56.228.356/0056-05   
1        3      77        2  12.347.831/0001-13   
2        3      77        3  08.285.194/0002-01   
3        3      77        4  10.631.721/0001-53   
4        3      77        5  07.652.868/0001-15   
5        3      77        6  02.808.708/0043-58   
6        3      77        7  02.808.708/0059-15   
7        3      77        8  02.808.708/0041-96   
8        3      77        9  11.371.020/0001-95   
9        3      77       10      054.438.901-82   

                        Situação na RF  \
0  ATIVA                                 
1                                        
2  ATIVA                                 
3                                        
4                                        
5                                        
6                                        
7                                        
8                                        
9                                        

                              Nome Fantasia  \
0  CDC Itumbiara                              
1  BLUE LOGISTICA TRANS                       
2  QUIOSQ.CHOPP BRAHMA                        
3  SUPERMERCADO DANTAS                        
4  BAR E LANC. EVENTOS                        
5  F. Cebrasa                                 
6  F. Brasilia                                
7  F. Goiania                                 
8  COMERCIAL GUERRA                           
9  LAZER CANECAO                              

                               Razão Social  \
0  CRBS S/A - CDC Itumbiara                   
1  BLUE LOGISTICA E TRANSPORTES LTDA          
2  CAVACO MATERIAL ESPORTIVO E CHOPERIA LTD   
3  LUCIANO DANTAS NETO                        
4  COSME ALVES SANTANA E CIA LTDA             
5  Cia de Bebidas das Americas - Ambev - F.   
6  Cia de Bebidas das Americas - Ambev - F.   
7  Cia de Bebidas das Americas - Ambev - F.   
8  COMERCIAL GUERRA SG LTDA ME                
9  ADEMAR ALVES PERREIRA                      

                                   Endereço  \
0  Av. Pres. Tancredo de Almeida Neve159      
1  AV PRESIDENTE TANCREDO DE ALMEIDA160       
2  AVN OSVALDO CRUZ 120                       
3  AV ARLINDO TEODORO MENDONCA 1              
4  AV AFONSO PENA 1890                        
5  Rod BR 060 110                             
6  Area Especial para Industria 1             
7  AV ario Veira Machado 2000                 
8  AV GOIAS 904                               
9  R GENI DA SILVA BARBOSA 1180               

                                Complemento  \
0                                             
1                                             
2  SHOPPING                                   
3   QUADRA 42 LOTE 1                          
4   A                                         
5   KM 110 a 114                              
6   SETOR LESTE                               
7                                             
8   QUADRA 42 LOTE 23                         
9                                             

                                              Bairro  \
0  SETOR BURITYS                                 ...   
1  SETOR BURITYS                                 ...   
2  SETOR RODOVIARIO                              ...   
3  JUQUINHA MENDON                               ...   
4  JARDIM AMERICA                                ...   
5  BOM SUCESSO                                   ...   
6  GAMA                                          ...   
7  JARDIM BALNEARIO MEIA PONTE                   ...   
8  OLIMPIA                                       ...   
9  SETOR PARANAIBA                               ...   

                           Cidade  UF         CEP  \
0  ITUMBIARA                       GO  75.516-195   
1  ITUMBIARA                       GO  75.516-195   
2  ITUMBIARA                       GO  75.516-020   
3  TURVELANDIA                     GO  75.970-000   
4  ITUMBIARA            

In [3]:
df['Filial'] = df['Filial'].astype(int)
df['Cód PDV'] = df['Cód PDV'].astype(int)
df['Concat'] = df['Filial'].map(str) +'_'+ df['Cód PDV'].map(str)

In [4]:
df2 = pd.read_json(r"C:\Users\99829465\Documents\120659.json", encoding="utf8")
df2.head(10)

tipo_filial                       cobra_adf_escalonado  unb_comercial  \
0         CDD                                                         0   
1         CDD                                                         0   
2         CDD  Não Cobra Adicional Financeiro Escalonado              0   
3         CDD  Não Cobra Adicional Financeiro Escalonado              0   
4         CDD      Cobra Adicional Financeiro Escalonado              0   
5         CDD  Não Cobra Adicional Financeiro Escalonado              0   
6         CDD      Cobra Adicional Financeiro Escalonado              0   
7         CDD      Cobra Adicional Financeiro Escalonado              0   
8         CDD      Cobra Adicional Financeiro Escalonado              0   
9         CDD      Cobra Adicional Financeiro Escalonado              0   

   valor_pago  titulo                       cobra_adf  valor_devido  \
0      588.00   57232                                        588.00   
1       16.00   57254                                         16.00   
2      663.04  201495  Não Cobra Adicional Financeiro        663.04   
3      318.24  197525      Cobra Adicional Financeiro        318.24   
4      335.54  200925      Cobra Adicional Financeiro        335.54   
5      774.40  189982  Não Cobra Adicional Financeiro        774.40   
6     1085.41  190724      Cobra Adicional Financeiro       1085.41   
7    21113.50  426581      Cobra Adicional Financeiro      21113.50   
8     1136.64  419033      Cobra Adicional Financeiro       1136.64   
9     1038.15  191138      Cobra Adicional Financeiro       1038.15   

   valor_pendente  forma_pagamento  cod_filial  adf_fixo  adf_escalonado  \
0             0.0                0         739      0.00             0.0   
1             0.0                0         739      0.00             0.0   
2             0.0                1           7      0.00             0.0   
3             0.0                4           7     11.35             0.0   
4             0.0                4           7      5.20             6.5   
5             0.0                1           7      0.00             0.0   
6             0.0                4           7      5.20             6.5   
7             0.0                4         455      5.20             6.5   
8             0.0                4         455      5.20             6.5   
9             0.0                4           7      5.20             6.5   

   original_specie  tipo_pagamento  GEO data_vencimento_original  cliente  \
0               13              13    1               2022-12-16       99   
1               13              13    1               2022-12-20       99   
2                1               1    1               2022-12-30      245   
3                4               4    1               2022-12-26      364   
4                4               4    1               2023-01-05      365   
5                1               1    1               2022-12-05      700   
6                4               4    1               2022-12-09      737   
7                4               4    1               2022-12-26     1001   
8                4               4    1               2022-12-19     1018   
9                4               4    1               2022-12-09     1152   

  data_emissao data_pagamento data_vencimento descricao_specie p_data_emissao  
0   2022-12-14     2023-01-03      2022-12-16             Vale     2022-12-01  
1   2022-12-16     2023-01-16      2022-12-20             Vale     2022-12-01  
2   2022-12-30     2022-12-30      2022-12-30    Venda a Vista     2022-12-01  
3   2022-12-22     2022-12-26      2022-12-26         Bloqueto     2022-12-01  
4   2022-12-29     2023-01-04      2023-01-05         Bloqueto     2022-12-01  
5   2022-12-05     2022-12-06      2022-12-05    Venda a Vista     2022-12-01  
6   2022-12-07     2022-12-07      2022-12-09         Bloqueto     2022-12-01  
7   2022-12-22     2022-12-26      2022-12-26         Bloqueto     20

In [5]:
df2['data_vencimento'] = pd.to_datetime(df2['data_vencimento'], format='%Y-%m-%d', errors='coerce')
df2['data_emissao'] = pd.to_datetime(df2['data_emissao'], format='%Y-%m-%d', errors='coerce')
df2['data_pagamento'] = pd.to_datetime(df2['data_pagamento'], format='%Y-%m-%d', errors='coerce')


Intervalo de datas: (2020 até d-1)

In [6]:
df2['cod_filial'] = df2['cod_filial'].astype(int)
df2['cliente'] = df2['cliente'].astype(int)
df2['Concat'] = df2['cod_filial'].map(str) +'_'+ df2['cliente'].map(str)

In [7]:
df3 = df2.loc[df2['cod_filial'] == 455]
df3.head()

tipo_filial                       cobra_adf_escalonado  unb_comercial  \
7          CDD      Cobra Adicional Financeiro Escalonado              0   
8          CDD      Cobra Adicional Financeiro Escalonado              0   
12         CDD  Não Cobra Adicional Financeiro Escalonado              0   
13         CDD  Não Cobra Adicional Financeiro Escalonado              0   
14         CDD      Cobra Adicional Financeiro Escalonado              0   

    valor_pago  titulo                       cobra_adf  valor_devido  \
7     21113.50  426581      Cobra Adicional Financeiro      21113.50   
8      1136.64  419033      Cobra Adicional Financeiro       1136.64   
12      247.60  434383  Não Cobra Adicional Financeiro        247.60   
13      152.90  419786  Não Cobra Adicional Financeiro        152.90   
14      193.04  423412      Cobra Adicional Financeiro        193.04   

    valor_pendente  forma_pagamento  cod_filial  adf_fixo  adf_escalonado  \
7              0.0                4         455       5.2             6.5   
8              0.0                4         455       5.2             6.5   
12             0.0                1         455       0.0             0.0   
13             0.0                1         455       0.0             0.0   
14             0.0                4         455       5.2             6.5   

    original_specie  tipo_pagamento  GEO data_vencimento_original  cliente  \
7                 4               4    1               2022-12-26     1001   
8                 4               4    1               2022-12-19     1018   
12                1               1    1               2022-12-29     1309   
13                1               1    1               2022-12-17     1516   
14                4               4    1               2022-12-26     1915   

   data_emissao data_pagamento data_vencimento descricao_specie  \
7    2022-12-22     2022-12-26      2022-12-26         Bloqueto   
8    2022-12-16     2022-12-19      2022-12-19         Bloqueto   
12   2022-12-29     2022-12-29      2022-12-29    Venda a Vista   
13   2022-12-17     2022-12-17      2022-12-17    Venda a Vista   
14   2022-12-20     2022-12-26      2022-12-26         Bloqueto   

   p_data_emissao    Concat  
7      2022-12-01  455_1001  
8      2022-12-01  455_1018  
12     2022-12-01  455_1309  
13     2022-12-01  455_1516  
14     2022-12-01  455_1915

In [8]:
df3.shape

(253555, 23)

In [9]:
df3 = df3.loc[df3["data_pagamento"] != ""]
df3.shape

(253555, 23)

In [10]:
df3["Atraso"] = np.where(df3['data_vencimento'] < df3['data_pagamento'],((df3['data_vencimento'] - df3['data_pagamento'])/pd.Timedelta(1, 'D')),0)
df3["Adiantamento"] = np.where(df3['data_vencimento'] >= df3['data_pagamento'],((df3['data_vencimento'] - df3['data_pagamento'])/pd.Timedelta(1, 'D')),0)

df3.head()

tipo_filial                       cobra_adf_escalonado  unb_comercial  \
7          CDD      Cobra Adicional Financeiro Escalonado              0   
8          CDD      Cobra Adicional Financeiro Escalonado              0   
12         CDD  Não Cobra Adicional Financeiro Escalonado              0   
13         CDD  Não Cobra Adicional Financeiro Escalonado              0   
14         CDD      Cobra Adicional Financeiro Escalonado              0   

    valor_pago  titulo                       cobra_adf  valor_devido  \
7     21113.50  426581      Cobra Adicional Financeiro      21113.50   
8      1136.64  419033      Cobra Adicional Financeiro       1136.64   
12      247.60  434383  Não Cobra Adicional Financeiro        247.60   
13      152.90  419786  Não Cobra Adicional Financeiro        152.90   
14      193.04  423412      Cobra Adicional Financeiro        193.04   

    valor_pendente  forma_pagamento  cod_filial  adf_fixo  adf_escalonado  \
7              0.0                4         455       5.2             6.5   
8              0.0                4         455       5.2             6.5   
12             0.0                1         455       0.0             0.0   
13             0.0                1         455       0.0             0.0   
14             0.0                4         455       5.2             6.5   

    original_specie  tipo_pagamento  GEO data_vencimento_original  cliente  \
7                 4               4    1               2022-12-26     1001   
8                 4               4    1               2022-12-19     1018   
12                1               1    1               2022-12-29     1309   
13                1               1    1               2022-12-17     1516   
14                4               4    1               2022-12-26     1915   

   data_emissao data_pagamento data_vencimento descricao_specie  \
7    2022-12-22     2022-12-26      2022-12-26         Bloqueto   
8    2022-12-16     2022-12-19      2022-12-19         Bloqueto   
12   2022-12-29     2022-12-29      2022-12-29    Venda a Vista   
13   2022-12-17     2022-12-17      2022-12-17    Venda a Vista   
14   2022-12-20     2022-12-26      2022-12-26         Bloqueto   

   p_data_emissao    Concat  Atraso  Adiantamento  
7      2022-12-01  455_1001     0.0           0.0  
8      2022-12-01  455_1018     0.0           0.0  
12     2022-12-01  455_1309     0.0           0.0  
13     2022-12-01  455_1516     0.0           0.0  
14     2022-12-01  455_1915     0.0           0.0

In [11]:
df3 = df3.merge(df,how='left',left_on='Concat',right_on='Concat')
df3.shape

(253555, 148)

In [12]:
df3 = df3.loc[df3['Prazo Atual']>0]
df3.shape

(195641, 148)

In [13]:
#df3_grouped = df3.groupby(by='Segmento NGE',as_index = False).agg({'valor_pendente' : 'sum' ,'Dias' : 'min'})

In [14]:
#df3['Retorno ADF'] = np.where(df3['Atraso']<0,df3['Receita ADF'] * ( df3['Atraso'] * -1),df3['Receita ADF'] * (1 + df3['Atraso']))

Ponderar receita adf pelo atraso ( de forma que atrasos sem ADF também prejudiquem)

In [15]:
df3 = df3.sort_values(by=['Concat', 'titulo'])

# Create a new column to represent the number of sales for each client
df3['sale_number'] = df3.groupby('Concat').cumcount() + 1

In [16]:
df3["ano"] = df3.data_pagamento.dt.year

df3["paymonth"] = df3.data_pagamento.dt.month
df3["paymonth"] = df3["paymonth"].map(str) +'_'+ df3['ano'].map(str)

In [17]:
df3["Segmento NGE"].unique()

array(['TRAD            ', 'VIP             ', 'SUB             ',
       'Rota            ', 'AS  1-4         ', 'AS  5           ',
       'Lj. Conveniencia', 'CENTRAL         ', 'OUTROS          ',
       'CDD             '], dtype=object)

In [18]:
df3['Prazo na Venda'] = (( df3['data_vencimento'] - df3['data_emissao'] )/pd.Timedelta(1, 'D'))

In [19]:
df3['adf_fixo']    =  df3['adf_fixo'] / 100
df3['Receita ADF'] = (df3['adf_fixo']/30)*df3['Prazo na Venda'] * df3['valor_pago']
df3.head()

tipo_filial                       cobra_adf_escalonado  unb_comercial  \
90339          CDD  Não Cobra Adicional Financeiro Escalonado              0   
235483         CDD      Cobra Adicional Financeiro Escalonado              0   
190626         CDD  Não Cobra Adicional Financeiro Escalonado              0   
218214         CDD      Cobra Adicional Financeiro Escalonado              0   
207439         CDD      Cobra Adicional Financeiro Escalonado              0   

        valor_pago  titulo                       cobra_adf  valor_devido  \
90339        41.26   46888  Não Cobra Adicional Financeiro         41.26   
235483      353.98   53630      Cobra Adicional Financeiro        353.98   
190626       31.90   61162  Não Cobra Adicional Financeiro         31.90   
218214      313.76   61163      Cobra Adicional Financeiro        313.76   
207439      384.27   96757      Cobra Adicional Financeiro        384.27   

        valor_pendente  forma_pagamento  cod_filial  adf_fixo  adf_escalonado  \
90339              0.0                1         455     0.000             0.0   
235483             0.0                4         455     0.052             0.0   
190626             0.0                1         455     0.000             0.0   
218214             0.0                4         455     0.052             0.0   
207439             0.0                4         455     0.052             0.0   

        original_specie  tipo_pagamento  GEO data_vencimento_original  \
90339                 1               1    1               2022-01-13   
235483                4               4    1               2022-01-24   
190626                1               1    1               2022-01-27   
218214                4               4    1               2022-01-31   
207439                4               4    1               2022-03-07   

        cliente data_emissao data_pagamento data_vencimento descricao_specie  \
90339     10002   2022-01-13     2022-01-29      2022-01-13    Venda a Vista   
235483    10002   2022-01-20     2022-01-24      2022-01-24         Bloqueto   
190626    10002   2022-01-27     2022-01-28      2022-01-27    Venda a Vista   
218214    10002   2022-01-27     2022-01-31      2022-01-31         Bloqueto   
207439    10002   2022-03-03     2022-03-07      2022-03-07         Bloqueto   

       p_data_emissao     Concat  Atraso  Adiantamento  Empresa  Filial  \
90339      2022-01-01  455_10002   -16.0           0.0     81.0   455.0   
235483     2022-01-01  455_10002     0.0           0.0     81.0   455.0   
190626     2022-01-01  455_10002    -1.0           0.0     81.0   455.0   
218214     2022-01-01  455_10002     0.0           0.0     81.0   455.0   
207439     2022-03-01  455_10002     0.0           0.0     81.0   455.0   

        Cód PDV           Documento                       Situação na RF  \
90339   10002.0  11.820.031/0001-05  ATIVA                                 
235483  10002.0  11.820.031/0001-05  ATIVA                                 
190626  10002.0  11.820.031/0001-05  ATIVA                                 
218214  10002.0  11.820.031/0001-05  ATIVA                                 
207439  10002.0  11.820.031/0001-05  ATIVA                                 

                                   Nome Fantasia  \
90339   SORVETERIA MARCOS                          
235483  SORVETERIA MARCOS                          
190626  SORVETERIA MARCOS                          
218214  SORVETERIA MARCOS                          
207439  SORVETERIA MARCOS                          

                                    Razão Social  \
90339   MARINALVA SILVA DOS SANTOS ME              
235483  MARINALVA SILVA DOS SANTOS ME              
190626  MARINALVA SILVA DOS SANTOS ME              
218214  MARINALVA SILVA DOS SANTOS ME              
207439  MARINALVA SILVA DOS SANTOS ME              

                                        Endereço  \
90339   R FREI CANUTO 365                          
235483  R FREI CANUTO 36

In [20]:
var_resume = 'Concat' # trocar para tipo, segmento NGE ou concat
df_pdvs = df3[['Concat','paymonth','Receita ADF', 'valor_pago','Filial','Segmento NGE','Tipo de Pessoa','Atraso','Adiantamento','Prazo na Venda']]
df_pdvs = df_pdvs.groupby([var_resume,'paymonth'],as_index = False).agg({'valor_pago' : 'sum' ,'Atraso': 'mean','Adiantamento': 'mean',
                                                                       'Prazo na Venda' : 'mean', 'Receita ADF' : 'sum'})
df_pdvs.head(20)

Concat     paymonth  valor_pago    Atraso  Adiantamento  \
0   455_10002   1.0_2022.0      740.90 -4.250000          0.00   
1   455_10002   1.0_2023.0     2755.62  0.000000          0.00   
2   455_10002  10.0_2022.0      747.40  0.000000          0.00   
3   455_10002  11.0_2022.0     2006.26  0.000000          0.00   
4   455_10002  12.0_2022.0     2807.70  0.000000          0.00   
5   455_10002   2.0_2021.0     1095.54  0.000000          0.00   
6   455_10002   3.0_2021.0     2252.12  0.000000          0.00   
7   455_10002   3.0_2022.0     1612.58  0.000000          0.00   
8   455_10002   4.0_2021.0      469.31  0.000000          0.00   
9   455_10002   4.0_2022.0      546.38  0.000000          0.00   
10  455_10002   6.0_2022.0     1634.12 -0.250000          0.25   
11  455_10002   7.0_2021.0     1631.91  0.000000          0.00   
12  455_10002   8.0_2021.0      192.64  0.000000          0.00   
13  455_10002   9.0_2022.0     1845.73  0.000000          0.00   
14  455_10002      nan_nan        0.00  0.000000          0.00   
15  455_10007   1.0_2022.0    35721.88  0.000000          0.00   
16  455_10007   1.0_2023.0    15212.24  0.000000          0.00   
17  455_10007  10.0_2022.0     5070.66  0.000000          0.00   
18  455_10007  11.0_2022.0    10302.51 -0.285714          0.00   
19  455_10007  12.0_2022.0     5931.29 -0.333333          0.00   

    Prazo na Venda  Receita ADF  
0         2.000000     4.629664  
1         5.666667    32.334773  
2         4.000000     5.181973  
3         7.000000    40.867516  
4         6.500000    52.361245  
5         6.000000     0.000000  
6         4.000000     1.249595  
7         3.750000    10.322468  
8         5.000000     4.067353  
9         4.000000     3.788235  
10        2.250000    11.189897  
11        4.000000    11.144259  
12        3.000000     1.001728  
13        4.000000    16.959269  
14        4.000000     0.000000  
15        8.000000   385.082553  
16        9.000000   335.977128  
17        7.000000    61.524008  
18        6.142857   139.917475  
19        5.000000    65.522323

In [21]:
df_pdvs['Valor Ponderado'] = (df_pdvs['Prazo na Venda'] * df_pdvs['valor_pago'])

In [22]:
df_meses = df_pdvs.groupby('paymonth',as_index = False).agg({'valor_pago' : 'sum' ,
                                                                         'Atraso': 'mean',
                                                                         'Adiantamento': 'mean',
                                                                         'Prazo na Venda' : 'mean', 
                                                                         'Receita ADF' : 'sum','Valor Ponderado' : 'sum'})
df_meses.head()


paymonth   valor_pago      Atraso  Adiantamento  Prazo na Venda  \
0   1.0_2021.0      2014.06    0.000000      2.000000        0.000000   
1   1.0_2022.0  39962747.61   -0.418153      0.649536        3.769424   
2   1.0_2023.0  27317492.62   -1.944721      0.150142        6.158629   
3  10.0_2021.0    117910.91 -111.569444      0.000000        2.250000   
4  10.0_2022.0  19454663.22   -1.496025      0.177374        6.310440   

     Receita ADF  Valor Ponderado  
0       0.000000     0.000000e+00  
1  461671.125349     2.763419e+08  
2  112128.183190     3.978669e+08  
3      22.514908     7.191033e+04  
4   83145.343157     2.541188e+08

In [23]:
df_meses['PMP'] =df_meses['Valor Ponderado']/(df_meses['valor_pago'])
df_meses.head()

paymonth   valor_pago      Atraso  Adiantamento  Prazo na Venda  \
0   1.0_2021.0      2014.06    0.000000      2.000000        0.000000   
1   1.0_2022.0  39962747.61   -0.418153      0.649536        3.769424   
2   1.0_2023.0  27317492.62   -1.944721      0.150142        6.158629   
3  10.0_2021.0    117910.91 -111.569444      0.000000        2.250000   
4  10.0_2022.0  19454663.22   -1.496025      0.177374        6.310440   

     Receita ADF  Valor Ponderado        PMP  
0       0.000000     0.000000e+00   0.000000  
1  461671.125349     2.763419e+08   6.914988  
2  112128.183190     3.978669e+08  14.564546  
3      22.514908     7.191033e+04   0.609870  
4   83145.343157     2.541188e+08  13.062105

In [24]:
df_pdvs.shape

(44616, 8)

In [25]:
dfaux = pd.merge(df_pdvs,df_meses, on='paymonth',copy=False,suffixes=['','_x'])
dfaux = dfaux[['Concat','paymonth',	'valor_pago'	,'Atraso',	'Adiantamento'	,'Prazo na Venda',	'Receita ADF'	,'Valor Ponderado',	'PMP']]

In [26]:
dfaux['Capital Investido'] = (dfaux['valor_pago'] * dfaux['PMP'])/30
dfaux.head()

Concat    paymonth  valor_pago  Atraso  Adiantamento  Prazo na Venda  \
0  455_10002  1.0_2022.0      740.90   -4.25           0.0             2.0   
1  455_10007  1.0_2022.0    35721.88    0.00           0.0             8.0   
2   455_1001  1.0_2022.0   183580.92    0.00           0.0             4.4   
3  455_10013  1.0_2022.0     2982.92    0.00           4.5             7.0   
4  455_10014  1.0_2022.0    16401.06    0.00           0.0             2.2   

   Receita ADF  Valor Ponderado       PMP  Capital Investido  
0     4.629664         1481.800  6.914988         170.777164  
1   385.082553       285775.040  6.914988        8233.879565  
2  1067.759333       807756.048  6.914988       42315.331267  
3    60.762080        20880.440  6.914988         687.561910  
4     0.000000        36082.332  6.914988        3780.438005

In [27]:
dfaux['ROIC'] = ((dfaux['Receita ADF'] + dfaux['Receita ADF'] * 0.11 ) / dfaux['Capital Investido']) 
dfaux.head(20)

Concat    paymonth  valor_pago    Atraso  Adiantamento  Prazo na Venda  \
0   455_10002  1.0_2022.0      740.90 -4.250000      0.000000        2.000000   
1   455_10007  1.0_2022.0    35721.88  0.000000      0.000000        8.000000   
2    455_1001  1.0_2022.0   183580.92  0.000000      0.000000        4.400000   
3   455_10013  1.0_2022.0     2982.92  0.000000      4.500000        7.000000   
4   455_10014  1.0_2022.0    16401.06  0.000000      0.000000        2.200000   
5   455_10018  1.0_2022.0     2271.28  0.000000      0.000000        4.000000   
6   455_10031  1.0_2022.0     1504.28  0.000000      0.000000        4.000000   
7   455_10033  1.0_2022.0     5743.44 -2.500000      1.250000        2.250000   
8   455_10035  1.0_2022.0     1429.08  0.000000      0.000000        0.000000   
9   455_10038  1.0_2022.0     8487.57 -0.333333      0.000000        5.000000   
10  455_10048  1.0_2022.0      725.20  0.000000      0.000000        0.000000   
11  455_10053  1.0_2022.0       65.80  0.000000      0.000000        0.000000   
12  455_10059  1.0_2022.0    29130.20  0.000000      0.000000        3.800000   
13  455_10062  1.0_2022.0    89084.34 -0.200000      0.000000        3.600000   
14  455_10063  1.0_2022.0     2194.71 -0.200000      0.000000        4.000000   
15  455_10066  1.0_2022.0     6300.04 -0.600000      0.000000        2.200000   
16  455_10069  1.0_2022.0    21075.27  0.000000      0.000000        3.000000   
17  455_10076  1.0_2022.0    26469.42  0.000000      0.000000        3.000000   
18  455_10081  1.0_2022.0    67379.48  0.000000      0.076923        3.153846   
19  455_10085  1.0_2022.0     5131.97  0.000000      0.000000        3.000000   

    Receita ADF  Valor Ponderado       PMP  Capital Investido      ROIC  
0      4.629664      1481.800000  6.914988         170.777164  0.030091  
1    385.082553    285775.040000  6.914988        8233.879565  0.051913  
2   1067.759333    807756.048000  6.914988       42315.331267  0.028009  
3     60.762080     20880.440000  6.914988         687.561910  0.098094  
4      0.000000     36082.332000  6.914988        3780.438005  0.000000  
5      0.000000      9085.120000  6.914988         523.529164  0.000000  
6     11.400133      6017.120000  6.914988         346.735960  0.036495  
7     65.441675     12922.740000  6.914988        1323.860705  0.054870  
8      0.000000         0.000000  6.914988         329.402389  0.000000  
9     73.558940     42437.850000  6.914988        1956.381612  0.041735  
10     0.000000         0.000000  6.914988         167.158320  0.000000  
11     0.000000         0.000000  6.914988          15.166875  0.000000  
12   199.025337    110694.760000  6.914988        6714.499867  0.032902  
13   732.047940    320703.624000  6.914988       20533.906017  0.039572  
14    16.645113      8778.840000  6.914988         505.879809  0.036523  
15    22.031188     13860.088000  6.914988        1452.156791  0.016840  
16   109.591404     63225.810000  6.914988        4857.841608  0.025041  
17   137.640984     79408.260000  6.914988        6101.191103  0.025041  
18   350.998752    212504.513846  6.914988       15530.944157  0.025086  
19    26.686244     15395.910000  6.914988        1182.917106  0.025041

In [28]:
smaller_dataframes = np.array_split(dfaux, 10)

# Print each smaller DataFrame
for idx, smaller_df in enumerate(smaller_dataframes):
    print(f"Smaller DataFrame {idx + 1}:\n{smaller_df}\n")
    

Smaller DataFrame 1:
         Concat    paymonth  valor_pago      Atraso  Adiantamento  \
0     455_10002  1.0_2022.0      740.90   -4.250000      0.000000   
1     455_10007  1.0_2022.0    35721.88    0.000000      0.000000   
2      455_1001  1.0_2022.0   183580.92    0.000000      0.000000   
3     455_10013  1.0_2022.0     2982.92    0.000000      4.500000   
4     455_10014  1.0_2022.0    16401.06    0.000000      0.000000   
5     455_10018  1.0_2022.0     2271.28    0.000000      0.000000   
6     455_10031  1.0_2022.0     1504.28    0.000000      0.000000   
7     455_10033  1.0_2022.0     5743.44   -2.500000      1.250000   
8     455_10035  1.0_2022.0     1429.08    0.000000      0.000000   
9     455_10038  1.0_2022.0     8487.57   -0.333333      0.000000   
10    455_10048  1.0_2022.0      725.20    0.000000      0.000000   
11    455_10053  1.0_2022.0       65.80    0.000000      0.000000   
12    455_10059  1.0_2022.0    29130.20    0.000000      0.000000   
13    455_100

In [29]:
#pivotar a tabela por cluster (retorno ADF/capitalinv do SUB,rota e etc.)
df2_pivoted = smaller_dataframes[0].pivot_table(index='Concat', columns='paymonth', values='ROIC', aggfunc='first')

# Reset the index to have 'client' as a regular column
df2_pivoted.reset_index(inplace=True)

# Rename the columns for clarity (optional)
df2_pivoted.columns.name = None

print(df2_pivoted)

         Concat  1.0_2022.0  1.0_2023.0
0     455_10002    0.030091    0.026829
1     455_10007    0.051913    0.050497
2      455_1001    0.028009    0.017669
3     455_10013    0.098094    0.023778
4     455_10014    0.000000         NaN
5     455_10018    0.000000         NaN
6     455_10031    0.036495         NaN
7     455_10033    0.054870    0.013414
8     455_10035    0.000000         NaN
9     455_10038    0.041735    0.019815
10    455_10048    0.000000    0.011889
11    455_10053    0.000000    0.066734
12    455_10059    0.032902         NaN
13    455_10062    0.039572    0.015852
14    455_10063    0.036523    0.025243
15    455_10066    0.016840    0.019815
16    455_10069    0.025041    0.017547
17    455_10076    0.025041    0.015852
18    455_10081    0.025086    0.011889
19    455_10085    0.025041         NaN
20    455_10087    0.000000    0.015852
21    455_10089    0.000000         NaN
22    455_10101    0.041735         NaN
23    455_10109    0.008347    0.011889


Precisamos:
- modelar da mesma forma por Receita ADF
- Calcular os Retornos
- aplicar no notebook de markowitz